In [12]:
import sys
sys.path.append("..")
from lib.util import add_race_eth,  add_income_group
import pandas as pd
pd.options.display.max_columns = 50
pd.options.display.max_rows = 1550
import numpy as np
from ambry import library
l = library()
p = l.get('ffiec.gov-hmda-2010e-lar-2012-ca').partition
df = p.select("SELECT * FROM lar WHERE county_code = 73").pandas

In [28]:
add_race_eth(df)
dfs = df[['id','census_tract_number', 'applicant_ethnicity','applicant_race_1', 'race_eth']]

In [29]:
ts = l.get('ffiec.gov-hmda-2010e-ts').partition.pandas
ts_name = ts[['respondent_id','respondent_name']]
x = df[['id','respondent_id', 'loan_type']].merge(ts_name, on='respondent_id')
x[x.respondent_name.str.contains('BANK OF AMERICA')][['respondent_id','respondent_name']].drop_duplicates()

respondent_id        respondent_name
0    0000480228  BANK OF AMERICA, N.A.

# BoA
- **Missing: Minority Status, Tract/BNA**

In [30]:
df = df[df.respondent_id=='0000480228'].copy()

###
# Action type == ALL
###
totalcount = df.loan_amount.count()
totalamount = df.loan_amount.sum()
df['loan_purtype'] = '_'
df[(df['loan_purpose'] == 1) & (df['loan_type'] == 1)].loan_purtype = 'Purchase - Conventional'
#df['loan_purtype'][(df['loan_purpose'] == 1) & (df['loan_type'] > 1)] = 'Purchase - Goverment'
df[(df['loan_purpose'] == 1) & (df['loan_type'] > 1)].loan_purtype = 'Purchase - Goverment'
df

id  year respondent_id  agency_code  loan_type  property_type  \
81599  1562393  2012    0000480228            9          3              1   
81600  1562394  2012    0000480228            9          1              1   
81601  1562395  2012    0000480228            9          1              1   
81602  1562396  2012    0000480228            9          3              1   
81603  1562397  2012    0000480228            9          1              1   
81604  1562398  2012    0000480228            9          1              1   
81605  1562399  2012    0000480228            9          1              1   
81606  1562400  2012    0000480228            9          1              1   
81607  1562401  2012    0000480228            9          1              1   
81608  1562402  2012    0000480228            9          1              1   
81609  1562403  2012    0000480228            9          1              1   
81610  1562404  2012    0000480228            9          1              1   
81611  1562405  2012    0000480228            9          1              1   
81612  1562406  2012    0000480228            9          1              1   
81613  1562407  2012    0000480228            9          1              1   
81614  1562408  2012    0000480228            9          1              1   
81615  1562409  2012    0000480228            9          1              1   
81616  1562410  2012    0000480228            9          1              1   
81617  1562411  2012    0000480228            9          3              1   
81618  1562412  2012    0000480228            9          1              1   
81619  1562413  2012    0000480228            9          3              1   
81620  1562414  2012    0000480228            9          1              1   
81621  1562415  2012    0000480228            9          1              1   
81622  1562416  2012    0000480228            9          1              1   
81623  1562417  2012    0000480228            9          1              1   
81624  1562418  2012    0000480228            9          1              1   
81625  1562419  2012    0000480228            9          1              1   
81626  1562420  2012    0000480228            9          3              1   
81627  1562421  2012    0000480228            9          1              1   
81628  1562422  2012    0000480228            9          1              1   
81629  1562423  2012    0000480228            9          1              1   
81630  1562424  2012    0000480228            9          1              1   
81631  1562425  2012    0000480228            9          3              1   
81632  1562426  2012    0000480228            9          1              1   
81633  1562427  2012    0000480228            9          2              1   
81634  1562428  2012    0000480228            9          1              1   
81635  1562429  2012    0000480228            9          1              1   
81636  1562430  2012    0000480228            9          2              1   
81637  1562431  2012    0000480228            9          1              1   
81638  1562432  2012    0000480228            9          1              1   
81639  1562433  2012    0000480228            9          1              1   
81640  1562434  2012    0000480228            9          1              1   
81641  1562435  2012    0000480228            9          3              1   
81642  1562436  2012    0000480228            9          1              1   
81643  1562437  2012    0000480228            9          1              1   
81644  1562438  2012    0000480228            9          1              1   
81645  1562439  2012    0000480228            9          1              1   
81646  1562440  2012    0000480228            9          1              1   
81647  1562441  2012    0000480228            9          1              1   
81648  1562442  2012    0000480228            9          3              1   
81649  1562443  2012    0000480228            9          1              1   
81650  1

In [16]:
### By Loan Purpose and Type

df['loan_purtype'][df['loan_purpose'] == 2] = 'Home Improvement'
df['loan_purtype'][df['loan_purpose'] == 3] = 'Refinancing'

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [17]:
loanpt = df.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum}).copy() 
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

In [18]:

def to_float(v):
    try:
        return float(v)
    except:
        return 0
     
df.loc[:,'applicant_income'] = df.apply(lambda row: to_float(row.applicant_income), axis=1)

### By Applicant Race/Ethnicity



race_eth  = df.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]

###By Applicant Income

df['applicant_income_percent_median'] = 100*df.applicant_income/df.applicant_income.median()
df['applicant_income_cat'] = 'Income Not Available'
df['applicant_income_cat'][df['applicant_income_percent_median'] < 50] = 'Low'
df['applicant_income_cat'][(df['applicant_income_percent_median'] >= 50) & (df['applicant_income_percent_median'] < 80)] = 'Moderate'
df['applicant_income_cat'][(df['applicant_income_percent_median'] >= 80) & (df['applicant_income_percent_median'] < 120)] = 'Middle'
df['applicant_income_cat'][df['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum}).copy()

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together

frames = [loanpt, race_eth,income,sex]
totalapp = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
totalapp
pieces = [totalapp.ix[:, ["count","%count","amount","%amount",]]]
totalapp = pd.concat(pieces, axis=1, keys=['Total Applications (1)'])
totalapp

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/k

Total Applications (1)                  \
                                                        count %count   amount   
Loan Purpose and Type Home Improvement                    103    1.0    32417   
                      Refinancing                        8271   83.2  2783718   
                      _                                  1572   15.8   658200   
Applicant Race/Eth    aian                                 40    0.4    11999   
                      as                                 1023   10.3   329398   
                      b                                   201    2.0    56321   
                      h                                  1463   14.7   354973   
                      pi                                   81    0.8    22402   
                      w                                  5668   57.0  2052423   
Applicant Income      Low                                2505   25.2   690161   
                      Middle                             1726   17.4   447785   
                      Moderate                           1583   15.9   340312   
                      Upper                              4132   41.5  1996077   
Applicant Sex         1                                  6979   70.2  2524987   
                      2                                  2324   23.4   645036   
                      3                                   620    6.2   255241   
                      4                                    23    0.2    49071   

                                                
                                       %amount  
Loan Purpose and Type Home Improvement     0.9  
                      Refinancing         80.1  
                      _                   18.9  
Applicant Race/Eth    aian                 0.3  
                      as                   9.5  
                      b                    1.6  
                      h                   10.2  
                      pi                   0.6  
                      w                   59.1  
Applicant Income      Low                 19.9  
                      Middle              12.9  
                      Moderate             9.8  
                      Upper               57.5  
Applicant Sex         1                   72.7  
                      2                   18.6  
                      3                    7.3  
                      4                    1.4

In [19]:
#######
# Action Type =1
#######
df1 = df[df.action_type==1]
totalcount = df1.loan_amount.count()
totalamount = df1.loan_amount.sum()

### By Loan Purpose and Type
df1['loan_purtype'] = '_'
df1['loan_purtype'][(df1['loan_purpose'] == 1) & (df1['loan_type'] == 1)] = 'Purchase - Conventional'
df1['loan_purtype'][(df1['loan_purpose'] == 1) & (df1['loan_type'] > 1)] = 'Purchase - Goverment'
df1['loan_purtype'][df1['loan_purpose'] == 2] = 'Home Improvement'
df1['loan_purtype'][df1['loan_purpose'] == 3] = 'Refinancing'

loanpt = df1.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

### By Applicant Race/Ethnicity

race_eth  = df1.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]


###By Applicant Income

df1['applicant_income_percent_median'] = 100*df1.applicant_income/df1.applicant_income.median()
df1['applicant_income_cat'] = 'Income Not Available'
df1['applicant_income_cat'][df1['applicant_income_percent_median'] < 50] = 'Low'
df1['applicant_income_cat'][(df1['applicant_income_percent_median'] >= 50) & (df1['applicant_income_percent_median'] < 80)] = 'Moderate'
df1['applicant_income_cat'][(df1['applicant_income_percent_median'] >= 80) & (df1['applicant_income_percent_median'] < 120)] = 'Middle'
df1['applicant_income_cat'][df1['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df1.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df1.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together

frames = [loanpt, race_eth,income,sex]
totalapp1 = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
pieces = [totalapp1.ix[:, ["count","%count","amount","%amount",]]]
totalapp1 = pd.concat(pieces, axis=1, keys=['Loan originated'])
totalapp1

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/pandas/core/generic.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_i

Loan originated                  \
                                                        count %count   amount   
Loan Purpose and Type Home Improvement                     52    0.8    17532   
                      Purchase - Conventional             622    9.8   294449   
                      Purchase - Goverment                243    3.8    81031   
                      Refinancing                        5439   85.6  1867375   
Applicant Race/Eth    aian                                 22    0.3     6991   
                      as                                  654   10.3   213490   
                      b                                   133    2.1    37938   
                      h                                   829   13.0   205775   
                      pi                                   49    0.8    14324   
                      w                                  3721   58.5  1358351   
Applicant Income      Low                                1669   26.3   460563   
                      Middle                             1070   16.8   279935   
                      Moderate                            953   15.0   203676   
                      Upper                              2664   41.9  1316213   
Applicant Sex         1                                  4546   71.5  1675143   
                      2                                  1414   22.2   404315   
                      3                                   381    6.0   162362   
                      4                                    15    0.2    18567   

                                                       
                                              %amount  
Loan Purpose and Type Home Improvement            0.8  
                      Purchase - Conventional    13.0  
                      Purchase - Goverment        3.6  
                      Refinancing                82.6  
Applicant Race/Eth    aian                        0.3  
                      as                          9.4  
                      b                           1.7  
                      h                           9.1  
                      pi                          0.6  
                      w                          60.1  
Applicant Income      Low                        20.4  
                      Middle                     12.4  
                      Moderate                    9.0  
                      Upper                      58.2  
Applicant Sex         1                          74.1  
                      2                          17.9  
                      3                           7.2  
                      4                           0.8

In [20]:
#######
# Action Type =2 
#######
df2 = df[df.action_type==2]
totalcount = df2.loan_amount.count()
totalamount = df2.loan_amount.sum()

### By Loan Purpose and Type

df2['loan_purtype'] = '_'
df2['loan_purtype'][(df2['loan_purpose'] == 1) & (df2['loan_type'] == 1)] = 'Purchase - Conventional'
df2['loan_purtype'][(df2['loan_purpose'] == 1) & (df2['loan_type'] > 1)] = 'Purchase - Goverment'
df2['loan_purtype'][df2['loan_purpose'] == 2] = 'Home Improvement'
df2['loan_purtype'][df2['loan_purpose'] == 3] = 'Refinancing'

loanpt = df2.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

### By Applicant Race/Ethnicity

race_eth  = df2.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]

###By Applicant Income

df2['applicant_income_percent_median'] = 100*df2.applicant_income/df2.applicant_income.median()
df2['applicant_income_cat'] = 'Income Not Available'
df2['applicant_income_cat'][df2['applicant_income_percent_median'] < 50] = 'Low'
df2['applicant_income_cat'][(df2['applicant_income_percent_median'] >= 50) & (df2['applicant_income_percent_median'] < 80)] = 'Moderate'
df2['applicant_income_cat'][(df2['applicant_income_percent_median'] >= 80) & (df2['applicant_income_percent_median'] < 120)] = 'Middle'
df2['applicant_income_cat'][df2['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df2.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df2.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together

frames = [loanpt, race_eth,income,sex]
totalapp2 = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
pieces = [totalapp2.ix[:, ["count","%count","amount","%amount",]]]
totalapp2 = pd.concat(pieces, axis=1, keys=['App approved but not accepted'])
totalapp2

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/p

App approved but not accepted  \
                                                                      count   
Loan Purpose and Type Home Improvement                                    1   
                      Purchase - Conventional                            43   
                      Refinancing                                       214   
Applicant Race/Eth    aian                                                1   
                      as                                                 27   
                      b                                                   1   
                      h                                                  23   
                      pi                                                  3   
                      w                                                 154   
Applicant Income      Low                                                67   
                      Middle                                             39   
                      Moderate                                           34   
                      Upper                                             118   
Applicant Sex         1                                                 160   
                      2                                                  72   
                      3                                                  25   
                      4                                                   1   

                                                                     
                                              %count amount %amount  
Loan Purpose and Type Home Improvement           0.4    546     0.5  
                      Purchase - Conventional   16.7  31246    30.1  
                      Refinancing               82.9  71990    69.4  
Applicant Race/Eth    aian                       0.4    310     0.3  
                      as                        10.5   7890     7.6  
                      b                          0.4    175     0.2  
                      h                          8.9   5658     5.5  
                      pi                         1.2    966     0.9  
                      w                         59.7  64096    61.8  
Applicant Income      Low                       26.0  18379    17.7  
                      Middle                    15.1  10474    10.1  
                      Moderate                  13.2   8022     7.7  
                      Upper                     45.7  66907    64.5  
Applicant Sex         1                         62.0  68462    66.0  
                      2                         27.9  20154    19.4  
                      3                          9.7  13866    13.4  
                      4                          0.4   1300     1.3

In [21]:
#######
# Action Type =3 
#######
df3 = df[df.action_type==3]
totalcount = df3.loan_amount.count()
totalamount = df3.loan_amount.sum()

### By Loan Purpose and Type

df3['loan_purtype'] = '_'
df3['loan_purtype'][(df3['loan_purpose'] == 1) & (df3['loan_type'] == 1)] = 'Purchase - Conventional'
df3['loan_purtype'][(df3['loan_purpose'] == 1) & (df3['loan_type'] > 1)] = 'Purchase - Goverment'
df3['loan_purtype'][df3['loan_purpose'] == 2] = 'Home Improvement'
df3['loan_purtype'][df3['loan_purpose'] == 3] = 'Refinancing'

loanpt = df3.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

### By Applicant Race/Ethnicity

race_eth  = df3.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]

###By Applicant Income

df3['applicant_income_percent_median'] = 100*df3.applicant_income/df3.applicant_income.median()
df3['applicant_income_cat'] = 'Income Not Available'
df3['applicant_income_cat'][df3['applicant_income_percent_median'] < 50] = 'Low'
df3['applicant_income_cat'][(df3['applicant_income_percent_median'] >= 50) & (df3['applicant_income_percent_median'] < 80)] = 'Moderate'
df3['applicant_income_cat'][(df3['applicant_income_percent_median'] >= 80) & (df3['applicant_income_percent_median'] < 120)] = 'Middle'
df3['applicant_income_cat'][df3['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df3.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df3.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together

frames = [loanpt, race_eth,income,sex]
totalapp3 = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
pieces = [totalapp3.ix[:, ["count","%count","amount","%amount",]]]
totalapp3 = pd.concat(pieces, axis=1, keys=['App denied by financial institution'])
totalapp3

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/p

App denied by financial institution  \
                                                                            count   
Loan Purpose and Type Home Improvement                                         35   
                      Purchase - Conventional                                 204   
                      Purchase - Goverment                                    100   
                      Refinancing                                            1577   
Applicant Race/Eth    aian                                                      8   
                      as                                                      203   
                      b                                                        36   
                      h                                                       331   
                      pi                                                       12   
                      w                                                      1032   
Applicant Income      Low                                                     476   
                      Middle                                                  309   
                      Moderate                                                294   
                      Upper                                                   837   
Applicant Sex         1                                                      1256   
                      2                                                       514   
                      3                                                       143   
                      4                                                         3   

                                                                      
                                              %count  amount %amount  
Loan Purpose and Type Home Improvement           1.8   10083     1.6  
                      Purchase - Conventional   10.6   80438    12.4  
                      Purchase - Goverment       5.2   32482     5.0  
                      Refinancing               82.3  524407    81.0  
Applicant Race/Eth    aian                       0.4    1679     0.3  
                      as                        10.6   58954     9.1  
                      b                          1.9    9744     1.5  
                      h                         17.3   79187    12.2  
                      pi                         0.6    2879     0.4  
                      w                         53.9  378001    58.4  
Applicant Income      Low                       24.8  119616    18.5  
                      Middle                    16.1   77715    12.0  
                      Moderate                  15.3   64234     9.9  
                      Upper                     43.7  385845    59.6  
Applicant Sex         1                         65.6  443748    68.5  
                      2                         26.8  141566    21.9  
                      3                          7.5   52712     8.1  
                      4                          0.2    9384     1.4

In [22]:
#######
# Action Type =4
#######
df4 = df[df.action_type==4]
totalcount = df4.loan_amount.count()
totalamount = df4.loan_amount.sum()

### By Loan Purpose and Type

df4['loan_purtype'] = '_'
df4['loan_purtype'][(df4['loan_purpose'] == 1) & (df4['loan_type'] == 1)] = 'Purchase - Conventional'
df4['loan_purtype'][(df4['loan_purpose'] == 1) & (df4['loan_type'] > 1)] = 'Purchase - Goverment'
df4['loan_purtype'][df4['loan_purpose'] == 2] = 'Home Improvement'
df4['loan_purtype'][df4['loan_purpose'] == 3] = 'Refinancing'

loanpt = df4.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

### By Applicant Race/Ethnicity

race_eth  = df4.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]

###By Applicant Income

df4['applicant_income_percent_median'] = 100*df4.applicant_income/df4.applicant_income.median()
df4['applicant_income_cat'] = 'Income Not Available'
df4['applicant_income_cat'][df4['applicant_income_percent_median'] < 50] = 'Low'
df4['applicant_income_cat'][(df4['applicant_income_percent_median'] >= 50) & (df4['applicant_income_percent_median'] < 80)] = 'Moderate'
df4['applicant_income_cat'][(df4['applicant_income_percent_median'] >= 80) & (df4['applicant_income_percent_median'] < 120)] = 'Middle'
df4['applicant_income_cat'][df4['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df4.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df4.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together

frames = [loanpt, race_eth,income,sex]
totalapp4 = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
pieces = [totalapp4.ix[:, ["count","%count","amount","%amount",]]]
totalapp4 = pd.concat(pieces, axis=1, keys=['App withdrawn by applicant'])
totalapp4

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/p

App withdrawn by applicant  \
                                                                   count   
Loan Purpose and Type Home Improvement                                 6   
                      Purchase - Conventional                        115   
                      Purchase - Goverment                            48   
                      Refinancing                                    601   
Applicant Race/Eth    aian                                             5   
                      as                                              88   
                      b                                               12   
                      h                                              136   
                      pi                                               7   
                      w                                              422   
Applicant Income      Low                                            174   
                      Middle                                         152   
                      Moderate                                       127   
                      Upper                                          317   
Applicant Sex         1                                              546   
                      2                                              180   
                      3                                               41   
                      4                                                3   

                                                                      
                                              %count  amount %amount  
Loan Purpose and Type Home Improvement           0.8     738     0.3  
                      Purchase - Conventional   14.9   61614    24.2  
                      Purchase - Goverment       6.2   16806     6.6  
                      Refinancing               78.1  175489    68.9  
Applicant Race/Eth    aian                       0.6    1292     0.5  
                      as                        11.4   28644    11.2  
                      b                          1.6    3165     1.2  
                      h                         17.7   29441    11.6  
                      pi                         0.9    1379     0.5  
                      w                         54.8  139075    54.6  
Applicant Income      Low                       22.6   56970    22.4  
                      Middle                    19.7   38661    15.2  
                      Moderate                  16.5   26531    10.4  
                      Upper                     41.2  132485    52.0  
Applicant Sex         1                         70.9  179212    70.4  
                      2                         23.4   42233    16.6  
                      3                          5.3   14882     5.8  
                      4                          0.4   18320     7.2

In [23]:
#######
# Action Type =5
#######

df5 = df[df.action_type==5]
totalcount = df5.loan_amount.count()
totalamount = df5.loan_amount.sum()

### By Loan Purpose and Type

df5['loan_purtype'] = '_'
df5['loan_purtype'][(df5['loan_purpose'] == 1) & (df5['loan_type'] == 1)] = 'Purchase - Conventional'
df5['loan_purtype'][(df5['loan_purpose'] == 1) & (df5['loan_type'] > 1)] = 'Purchase - Goverment'
df5['loan_purtype'][df5['loan_purpose'] == 2] = 'Home Improvement'
df5['loan_purtype'][df5['loan_purpose'] == 3] = 'Refinancing'

loanpt = df5.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

### By Applicant Race/Ethnicity

race_eth  = df5.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]

###By Applicant Income

df5['applicant_income_percent_median'] = 100*df5.applicant_income/df5.applicant_income.median()
df5['applicant_income_cat'] = 'Income Not Available'
df5['applicant_income_cat'][df5['applicant_income_percent_median'] < 50] = 'Low'
df5['applicant_income_cat'][(df5['applicant_income_percent_median'] >= 50) & (df5['applicant_income_percent_median'] < 80)] = 'Moderate'
df5['applicant_income_cat'][(df5['applicant_income_percent_median'] >= 80) & (df5['applicant_income_percent_median'] < 120)] = 'Middle'
df5['applicant_income_cat'][df5['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df5.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df5.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together

frames = [loanpt, race_eth,income,sex]
totalapp5 = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
pieces = [totalapp5.ix[:, ["count","%count","amount","%amount",]]]
totalapp5 = pd.concat(pieces, axis=1, keys=['File closed for incompleteness'])
totalapp5

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/p

File closed for incompleteness  \
                                                                       count   
Loan Purpose and Type Home Improvement                                     6   
                      Purchase - Conventional                             13   
                      Purchase - Goverment                                 5   
                      Refinancing                                        296   
Applicant Race/Eth    aian                                                 1   
                      as                                                  36   
                      b                                                   10   
                      h                                                   66   
                      pi                                                   4   
                      w                                                  164   
Applicant Income      Low                                                 76   
                      Middle                                              55   
                      Moderate                                            46   
                      Upper                                              143   
Applicant Sex         1                                                  228   
                      2                                                   73   
                      3                                                   18   
                      4                                                    1   

                                                                      
                                              %count  amount %amount  
Loan Purpose and Type Home Improvement           1.9    2554     2.2  
                      Purchase - Conventional    4.1    4072     3.5  
                      Purchase - Goverment       1.6    1701     1.5  
                      Refinancing               92.5  106825    92.8  
Applicant Race/Eth    aian                       0.3     227     0.2  
                      as                        11.2   15054    13.1  
                      b                          3.1    2870     2.5  
                      h                         20.6   15568    13.5  
                      pi                         1.2    1192     1.0  
                      w                         51.2   62328    54.1  
Applicant Income      Low                       23.8   21236    18.4  
                      Middle                    17.2   13488    11.7  
                      Moderate                  14.4    9391     8.2  
                      Upper                     44.7   71037    61.7  
Applicant Sex         1                         71.2   88855    77.2  
                      2                         22.8   17452    15.2  
                      3                          5.6    7345     6.4  
                      4                          0.3    1500     1.3

In [24]:
#######
# Action Type = 6
#######

df6 = df[df.action_type==6]
totalcount = df6.loan_amount.count()
totalamount = df6.loan_amount.sum()

### By Loan Purpose and Type

df6['loan_purtype'] = '_'
df6['loan_purtype'][(df6['loan_purpose'] == 1) & (df6['loan_type'] == 1)] = 'Purchase - Conventional'
df6['loan_purtype'][(df6['loan_purpose'] == 1) & (df6['loan_type'] > 1)] = 'Purchase - Goverment'
df6['loan_purtype'][df6['loan_purpose'] == 2] = 'Home Improvement'
df6['loan_purtype'][df6['loan_purpose'] == 3] = 'Refinancing'

loanpt = df6.groupby(['loan_purtype'])
loanpt = loanpt['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})
loanpt['%count'] = np.round(100*loanpt['count']/totalcount,1)
loanpt['%amount'] = np.round(100*loanpt['amount']/totalamount,1)
loanpt=loanpt[['count','%count','amount','%amount']]

### By Applicant Race/Ethnicity

race_eth  = df6.groupby(['race_eth'])
race_eth  = race_eth ['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

race_eth ['%count'] = np.round(100*race_eth['count']/totalcount,1)
race_eth ['%amount'] = np.round(100*race_eth['amount']/totalamount,1)
race_eth = race_eth [['count','%count','amount','%amount']]

###By Applicant Income

df6['applicant_income_percent_median'] = 100*df6.applicant_income/df6.applicant_income.median()
df6['applicant_income_cat'] = 'Income Not Available'
df6['applicant_income_cat'][df6['applicant_income_percent_median'] < 50] = 'Low'
df6['applicant_income_cat'][(df6['applicant_income_percent_median'] >= 50) & (df6['applicant_income_percent_median'] < 80)] = 'Moderate'
df6['applicant_income_cat'][(df6['applicant_income_percent_median'] >= 80) & (df6['applicant_income_percent_median'] < 120)] = 'Middle'
df6['applicant_income_cat'][df6['applicant_income_percent_median'] >= 120] = 'Upper'

income  = df6.groupby(['applicant_income_cat'])
income   = income['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

income ['%count'] = np.round(100*income['count']/totalcount,1)
income ['%amount'] = np.round(100*income['amount']/totalamount,1)
income = income [['count','%count','amount','%amount']]

###By Applicant Sex

sex  = df6.groupby(['applicant_sex'])
sex   = sex['loan_amount'].agg(
                            {'count': np.size,
                             'amount': np.sum})

sex ['%count'] = np.round(100*sex['count']/totalcount,1)
sex ['%amount'] = np.round(100*sex['amount']/totalamount,1)
sex = sex [['count','%count','amount','%amount']]

### Smashing Tables Together
frames = [loanpt, race_eth,income,sex]
totalapp6 = pd.concat(frames, keys=['Loan Purpose and Type', 
                                   'Applicant Race/Eth', 
                                   'Applicant Income',
                                   'Applicant Sex'])
pieces = [totalapp6.ix[:, ["count","%count","amount","%amount",]]]
totalapp6 = pd.concat(pieces, axis=1, keys=['Loan purchased by institution'])
totalapp6

/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/proj/virt/ambry-prod/lib/python2.7/site-packages/IPython/kernel/__main__.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/eric/p

Loan purchased by institution  \
                                                                      count   
Loan Purpose and Type Home Improvement                                    3   
                      Purchase - Conventional                            25   
                      Purchase - Goverment                              154   
                      Refinancing                                       144   
Applicant Race/Eth    aian                                                3   
                      as                                                 15   
                      b                                                   9   
                      h                                                  78   
                      pi                                                  6   
                      w                                                 175   
Applicant Income      Low                                                48   
                      Middle                                            102   
                      Moderate                                           61   
                      Upper                                             115   
Applicant Sex         1                                                 243   
                      2                                                  71   
                      3                                                  12   

                                                                     
                                              %count amount %amount  
Loan Purpose and Type Home Improvement           0.9    964     1.0  
                      Purchase - Conventional    7.7  12195    13.1  
                      Purchase - Goverment      47.2  42166    45.4  
                      Refinancing               44.2  37632    40.5  
Applicant Race/Eth    aian                       0.9   1500     1.6  
                      as                         4.6   5366     5.8  
                      b                          2.8   2429     2.6  
                      h                         23.9  19344    20.8  
                      pi                         1.8   1662     1.8  
                      w                         53.7  50572    54.4  
Applicant Income      Low                       14.7  16091    17.3  
                      Middle                    31.3  25323    27.2  
                      Moderate                  18.7  10228    11.0  
                      Upper                     35.3  41315    44.4  
Applicant Sex         1                         74.5  69567    74.8  
                      2                         21.8  19316    20.8  
                      3                          3.7   4074     4.4

In [25]:
#Merging ALL
total = pd.concat([totalapp,totalapp1,totalapp2,totalapp3,totalapp4,totalapp5,totalapp6], axis=1)
total

Total Applications (1)         \
                                                               count %count   
Applicant Income      Low                                       2505   25.2   
                      Middle                                    1726   17.4   
                      Moderate                                  1583   15.9   
                      Upper                                     4132   41.5   
Applicant Race/Eth    aian                                        40    0.4   
                      as                                        1023   10.3   
                      b                                          201    2.0   
                      h                                         1463   14.7   
                      pi                                          81    0.8   
                      w                                         5668   57.0   
Applicant Sex         1                                         6979   70.2   
                      2                                         2324   23.4   
                      3                                          620    6.2   
                      4                                           23    0.2   
Loan Purpose and Type Home Improvement                           103    1.0   
                      Purchase - Conventional                    NaN    NaN   
                      Purchase - Goverment                       NaN    NaN   
                      Refinancing                               8271   83.2   
                      _                                         1572   15.8   

                                                                \
                                                amount %amount   
Applicant Income      Low                       690161    19.9   
                      Middle                    447785    12.9   
                      Moderate                  340312     9.8   
                      Upper                    1996077    57.5   
Applicant Race/Eth    aian                       11999     0.3   
                      as                        329398     9.5   
                      b                          56321     1.6   
                      h                         354973    10.2   
                      pi                         22402     0.6   
                      w                        2052423    59.1   
Applicant Sex         1                        2524987    72.7   
                      2                         645036    18.6   
                      3                         255241     7.3   
                      4                          49071     1.4   
Loan Purpose and Type Home Improvement           32417     0.9   
                      Purchase - Conventional      NaN     NaN   
                      Purchase - Goverment         NaN     NaN   
                      Refinancing              2783718    80.1   
                      _                         658200    18.9   

                                              Loan originated                  \
                                                        count %count   amount   
Applicant Income      Low                                1669   26.3   460563   
                      Middle                             1070   16.8   279935   
                      Moderate                            953   15.0   203676   
                      Upper                              2664   41.9  1316213   
Applicant Race/Eth    aian                                 22    0.3     6991   
                      as                                  654   10.3   213490   
                      b                                   133    2.1    37938   
                      h                                   829   13.0   205775   
                      pi                                   49    0.8    14324   
                      w                                  3721   58.5  1358351   
Applicant Sex         1    

In [27]:
boa.to_csv('boa.csv')

NameError: name 'boa' is not defined